In [43]:
#import dependencies
import pandas as pd
import json
import requests
import numpy as np

In [44]:
Rental_df = pd.read_csv("../resources/Rental Data.csv")
Vacancy_df = pd.read_csv("../resources/Vacancy Rate Data.csv")
Number_of_units_df = pd.read_csv("../resources/Number of Units Data.csv")

In [45]:
# rename and reorder columns for rental data
Rental_df = Rental_df.rename(columns = {  'Bachelor': 'AR Bachelor', '1 Bedroom': 'AR 1 Bedroom' , '2 Bedroom' : 'AR 2 Bedroom', '3 Bedroom +': 'AR 3 Bedroom +', 'Total' : 'AR Total', 'Dwelling Type ' : 'Dwelling Type'})
Rental_df.keys()

Rental_df = Rental_df[['Province', 'Centres', 'Zones', 'Neighbourhood', 'Dwelling Type',
       'AR Bachelor', 'AR 1 Bedroom', 'AR 2 Bedroom', 'AR 3 Bedroom +', 'AR Total',
       'Year']]
Rental_df.keys()

# rename and reorder columns for vacancy data
Vacancy_df = Vacancy_df.rename(columns = {  'Bachelor': 'VR Bachelor', '1 Bedroom': 'VR 1 Bedroom' , '2 Bedroom' : 'VR 2 Bedroom', '3 Bedroom +': 'VR 3 Bedroom +', 'Total' : 'VR Total', 'Dwelling Type ' : 'Dwelling Type'})
Vacancy_df.keys()

Vacancy_df = Vacancy_df[['Province', 'Centres', 'Zones', 'Neighbourhood', 'Dwelling Type',
       'VR Bachelor', 'VR 1 Bedroom', 'VR 2 Bedroom', 'VR 3 Bedroom +',
       'VR Total', 'Year']]
Vacancy_df.keys()

# rename and reorder columns for number of data
Number_of_units_df = Number_of_units_df.rename(columns = {  'Bachelor': 'Units Bachelor', '1 Bedroom': 'Units 1 Bedroom' , '2 Bedroom' : 'Units 2 Bedroom', '3 Bedroom +': 'Units 3 Bedroom +', 'Total' : 'Units Total', 'Dwelling Type ' : 'Dwelling Type'})
Number_of_units_df.keys()

Number_of_units_df = Number_of_units_df[['Province', 'Centres', 'Zones', 'Neighbourhood', 'Dwelling Type',
       'Units Bachelor', 'Units 1 Bedroom', 'Units 2 Bedroom',
       'Units 3 Bedroom +', 'Units Total', 'Year']]
Number_of_units_df.keys()

Index(['Province', 'Centres', 'Zones', 'Neighbourhood', 'Dwelling Type',
       'Units Bachelor', 'Units 1 Bedroom', 'Units 2 Bedroom',
       'Units 3 Bedroom +', 'Units Total', 'Year'],
      dtype='object')

In [46]:
Combined_df = pd.merge(Rental_df, Vacancy_df, on = ['Province','Centres','Zones','Neighbourhood','Dwelling Type','Year'],  how = 'left')

In [47]:
Combined_df = pd.merge(Combined_df, Number_of_units_df, on = ['Province','Centres','Zones','Neighbourhood','Dwelling Type','Year'],  how = 'left')

In [48]:
Combined_df.head()

Province     Centres             Zones     Neighbourhood Dwelling Type  \
0  Nfld.Lab.  St. John's   St. John's East   St. John's East           Row   
1  Nfld.Lab.  St. John's   St. John's East   St. John's East   Apt & Other   
2  Nfld.Lab.  St. John's   St. John's West   St. John's West           Row   
3  Nfld.Lab.  St. John's   St. John's West   St. John's West   Apt & Other   
4  Nfld.Lab.  St. John's  Remainder of CMA  Remainder of CMA           Row   

   AR Bachelor  AR 1 Bedroom  AR 2 Bedroom  AR 3 Bedroom +  AR Total  ...  \
0          0.0         783.0         943.0             0.0    1166.0  ...   
1        664.0         829.0        1049.0          1002.0     941.0  ...   
2          0.0           0.0         743.0             0.0     576.0  ...   
3        762.0         773.0         881.0           959.0     839.0  ...   
4          0.0           0.0           0.0             0.0       0.0  ...   

   VR Bachelor  VR 1 Bedroom  VR 2 Bedroom  VR 3 Bedroom +  VR Total  \
0          0.0           0.0           0.0             0.0       0.0   
1          0.0           3.9           6.4             5.2       5.6   
2          0.0           0.0           0.0             0.0       1.5   
3          3.9           6.1           6.1             0.0       6.2   
4          0.0           0.0           0.0             0.0       0.0   

   Units Bachelor  Units 1 Bedroom  Units 2 Bedroom  Units 3 Bedroom +  \
0             1.0             22.0             16.0               16.0   
1           203.0            641.0           1015.0              107.0   
2             0.0             46.0             21.0                0.0   
3           149.0            427.0            859.0              126.0   
4             0.0              0.0             64.0                6.0   

   Units Total  
0         55.0  
1       1966.0  
2         67.0  
3       1561.0  
4         70.0  

[5 rows x 21 columns]

In [49]:
Combined_df.keys()

Index(['Province', 'Centres', 'Zones', 'Neighbourhood', 'Dwelling Type',
       'AR Bachelor', 'AR 1 Bedroom', 'AR 2 Bedroom', 'AR 3 Bedroom +',
       'AR Total', 'Year', 'VR Bachelor', 'VR 1 Bedroom', 'VR 2 Bedroom',
       'VR 3 Bedroom +', 'VR Total', 'Units Bachelor', 'Units 1 Bedroom',
       'Units 2 Bedroom', 'Units 3 Bedroom +', 'Units Total'],
      dtype='object')

In [50]:
province_centres_lat_log = Combined_df.groupby(["Province","Centres"]).count()["Year"].to_frame().reset_index()

province_centres_lat_log['Lat'] = ''
province_centres_lat_log['Lon'] = ''

province_centres_lat_log = province_centres_lat_log[["Province", "Centres", "Lat", "Lon"]]
province_centres_lat_log.head()

Province               Centres Lat Lon
0     Alta               Calgary        
1     Alta              Edmonton        
2     Alta            Lethbridge        
3     B.C.  Abbotsford - Mission        
4     B.C.               Kelowna

In [51]:
base_url = "https://api.geoapify.com/v1/geocode/search?"
params = {
            "text":"",
             "type": "city",
             "format":"json",
             "apiKey": "<YOUR API KEY>"
        }

for index, row in province_centres_lat_log.iterrows():
    
    # Create search query, make request and store in json
    params["text"] = f"{row['Centres']}, Canada"
    response = requests.get(base_url, params).json()
    
    try:
        province_centres_lat_log.loc[index, "Lat"] = response['results'][0]['lat']
        province_centres_lat_log.loc[index, "Lon"] = response['results'][0]['lon']
    except:
        print("City not found. Skipping...")
        pass

    
# Indicate that Data Loading is complete 
print("-----------------------------")
print("Data Retrieval Complete      ")
print("-----------------------------")

-----------------------------
Data Retrieval Complete      
-----------------------------


In [52]:
Combined_df = pd.merge(Combined_df, province_centres_lat_log, on = ['Province','Centres'],  how = 'left')

In [53]:
Combined_df.head()

Province     Centres             Zones     Neighbourhood Dwelling Type  \
0  Nfld.Lab.  St. John's   St. John's East   St. John's East           Row   
1  Nfld.Lab.  St. John's   St. John's East   St. John's East   Apt & Other   
2  Nfld.Lab.  St. John's   St. John's West   St. John's West           Row   
3  Nfld.Lab.  St. John's   St. John's West   St. John's West   Apt & Other   
4  Nfld.Lab.  St. John's  Remainder of CMA  Remainder of CMA           Row   

   AR Bachelor  AR 1 Bedroom  AR 2 Bedroom  AR 3 Bedroom +  AR Total  ...  \
0          0.0         783.0         943.0             0.0    1166.0  ...   
1        664.0         829.0        1049.0          1002.0     941.0  ...   
2          0.0           0.0         743.0             0.0     576.0  ...   
3        762.0         773.0         881.0           959.0     839.0  ...   
4          0.0           0.0           0.0             0.0       0.0  ...   

   VR 2 Bedroom  VR 3 Bedroom +  VR Total  Units Bachelor  Units 1 Bedroom  \
0           0.0             0.0       0.0             1.0             22.0   
1           6.4             5.2       5.6           203.0            641.0   
2           0.0             0.0       1.5             0.0             46.0   
3           6.1             0.0       6.2           149.0            427.0   
4           0.0             0.0       0.0             0.0              0.0   

   Units 2 Bedroom  Units 3 Bedroom +  Units Total       Lat        Lon  
0             16.0               16.0         55.0  47.56147 -52.712616  
1           1015.0              107.0       1966.0  47.56147 -52.712616  
2             21.0                0.0         67.0  47.56147 -52.712616  
3            859.0              126.0       1561.0  47.56147 -52.712616  
4             64.0                6.0         70.0  47.56147 -52.712616  

[5 rows x 23 columns]

In [54]:
def getRentalData(row):
    dict = {}

    ar_dict = {}
    ar_dict["Bachelor"] = row["AR Bachelor"]
    ar_dict["1br"] = row["AR 1 Bedroom"]
    ar_dict["2br"] = row["AR 2 Bedroom"]
    ar_dict["3br+"] = row["AR 3 Bedroom +"]
    ar_dict["Total"] = row["AR Total"]

    dict["AverageRent"] = ar_dict

    vr_dict = {}

    vr_dict["Bachelor"] = row["VR Bachelor"]
    vr_dict["1br"] = row["VR 1 Bedroom"]
    vr_dict["2br"] = row["VR 2 Bedroom"]
    vr_dict["3br+"] = row["VR 3 Bedroom +"]
    vr_dict["Total"] = row["VR Total"]

    dict["VacancyRate"] = vr_dict

    nou_dict = {}

    nou_dict["Bachelor"] = row["Units Bachelor"]
    nou_dict["1br"] = row["Units 1 Bedroom"]
    nou_dict["2br"] = row["Units 2 Bedroom"]
    nou_dict["3br+"] = row["Units 3 Bedroom +"]
    nou_dict["Total"] = row["Units Total"]

    dict["NumberofUnits"] = nou_dict

    return dict
    

In [55]:
rental_data = []

for index, row in Combined_df.iterrows():
    dict = {}

    geo_dict = {}
    geo_dict["lat"] = row["Lat"]
    geo_dict["lon"] = row["Lon"]

    location_dict = {}

    location_dict["Province"] = row["Province"]
    location_dict["Center"] = row["Centres"]
    location_dict["CenterGeo"] = geo_dict
    location_dict["Zone"] = row["Zones"]
    location_dict["Neighbourhood"] = row["Neighbourhood"]
    

    dict["id"] = index + 1000
    dict["Location"] = location_dict

    dict["DwellingType"] = row["Dwelling Type"]
    dict["Year"] = row["Year"]

    dict["RentalInformation"] = getRentalData(row)

    rental_data.append(dict)

print(rental_data)

[{'id': 1000, 'Location': {'Province': 'Nfld.Lab.', 'Center': "St. John's", 'CenterGeo': {'lat': 47.5614705, 'lon': -52.7126162}, 'Zone': "St. John's East", 'Neighbourhood': "St. John's East"}, 'DwellingType': 'Row', 'Year': 2018, 'RentalInformation': {'AverageRent': {'Bachelor': 0.0, '1br': 783.0, '2br': 943.0, '3br+': 0.0, 'Total': 1166.0}, 'VacancyRate': {'Bachelor': 0.0, '1br': 0.0, '2br': 0.0, '3br+': 0.0, 'Total': 0.0}, 'NumberofUnits': {'Bachelor': 1.0, '1br': 22.0, '2br': 16.0, '3br+': 16.0, 'Total': 55.0}}}, {'id': 1001, 'Location': {'Province': 'Nfld.Lab.', 'Center': "St. John's", 'CenterGeo': {'lat': 47.5614705, 'lon': -52.7126162}, 'Zone': "St. John's East", 'Neighbourhood': "St. John's East"}, 'DwellingType': 'Apt & Other', 'Year': 2018, 'RentalInformation': {'AverageRent': {'Bachelor': 664.0, '1br': 829.0, '2br': 1049.0, '3br+': 1002.0, 'Total': 941.0}, 'VacancyRate': {'Bachelor': 0.0, '1br': 3.9, '2br': 6.4, '3br+': 5.2, 'Total': 5.6}, 'NumberofUnits': {'Bachelor': 203.0

In [56]:
with open('../output/rental_data.json', 'w') as file:
    file.write(json.dumps(rental_data, indent=4))